### Bronze  - Raw Ingestion (Raw, auditable, re-playable)
### Silver - Cleaning & Validation (Clean, trusted, analytics-ready)
### Gold - Business Aggregates (Business-ready, KPI-focused)

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window
from pyspark.sql.functions import lit

In [0]:
%fs
ls /Volumes/workspace/ecommerce/ecommerce_data

path name size modificationTime dbfs:/Volumes/workspace/ecommerce/ecommerce_data/2019-Nov.csv 2019-Nov.csv 9006762395 1767962633000 dbfs:/Volumes/workspace/ecommerce/ecommerce_data/2019-Oct.csv 2019-Oct.csv 5668612855 1767962553000 dbfs:/Volumes/workspace/ecommerce/ecommerce_data/delta/ delta/ 0 1768403081572 dbfs:/Volumes/workspace/ecommerce/ecommerce_data/incremental/ incremental/ 0 1768403081572 dbfs:/Volumes/workspace/ecommerce/ecommerce_data/parquet/ parquet/ 0 1768403081572

In [0]:
df_oct = spark.read.parquet("/Volumes/workspace/ecommerce/ecommerce_data/parquet/oct/")
df_oct.limit(5).show()

+-------------------+----------+----------+-------------------+--------------------+--------+-------+---------+--------------------+
|         event_time|event_type|product_id|        category_id|       category_code|   brand|  price|  user_id|        user_session|
+-------------------+----------+----------+-------------------+--------------------+--------+-------+---------+--------------------+
|2019-10-13 06:25:46|      view|   1002544|2053013555631882655|electronics.smart...|   apple| 460.51|518958788|e7e27c5c-1e78-481...|
|2019-10-13 06:25:46|      view|   3700301|2053013565983425517|appliances.enviro...|   vitek| 120.93|557977070|7afc206c-7259-4be...|
|2019-10-13 06:25:46|      view|  49100004|2127425375913902544|                NULL|    NULL|  45.05|514456508|9d6837a5-40df-49d...|
|2019-10-13 06:25:46|      view|   9200409|2053013552913973497|computers.periphe...|defender|  12.56|512530774|df2d048d-c1ae-41b...|
|2019-10-13 06:25:46|      view|   1306558|2053013558920217191|  comp

In [0]:
# BRONZE: Raw ingestion
bronze_df = spark.read.csv("/Volumes/workspace/ecommerce/ecommerce_data/2019-Oct.csv",header=True,inferSchema=True)

In [0]:
bronze_df.write.format("delta").mode("overwrite").saveAsTable("workspace.ecommerce.bronze_events_oct")

In [0]:
%sql
SELECT COUNT(*) FROM workspace.ecommerce.bronze_events_oct;

COUNT(*) 42448764

In [0]:
bronze_df = spark.table("workspace.ecommerce.bronze_events_oct")

In [0]:
from pyspark.sql.functions import col, to_timestamp

silver_df = bronze_df \
    .withColumn("event_time", to_timestamp(col("event_time"))) \
    .filter(col("event_time").isNotNull()) \
    .filter(col("user_session").isNotNull()) \
    .filter(col("product_id").isNotNull())

In [0]:
silver_df.write.format("delta") \
    .mode("overwrite") \
    .saveAsTable("workspace.ecommerce.silver_events")

In [0]:
%sql
SELECT COUNT(*) FROM workspace.ecommerce.silver_events;

COUNT(*) 42448762

In [0]:
from pyspark.sql.functions import sum, when

gold_funnel_df = silver_df.groupBy("product_id").agg(
    sum(when(col("event_type") == "view", 1).otherwise(0)).alias("views"),
    sum(when(col("event_type") == "cart", 1).otherwise(0)).alias("carts"),
    sum(when(col("event_type") == "purchase", 1).otherwise(0)).alias("purchases")
)

In [0]:
gold_funnel_df.write.format("delta") \
    .mode("overwrite") \
    .saveAsTable("workspace.ecommerce.gold_product_funnel")

In [0]:
gold_revenue_df = silver_df.filter(col("event_type") == "purchase") \
    .groupBy("category_code") \
    .agg(sum("price").alias("total_revenue"))

In [0]:
gold_revenue_df.write.format("delta") \
    .mode("overwrite") \
    .saveAsTable("workspace.ecommerce.gold_revenue_by_category")

In [0]:
%sql
SELECT COUNT(*) FROM workspace.ecommerce.gold_revenue_by_category;

COUNT(*) 122

In [0]:
%sql
SELECT COUNT(*) FROM workspace.ecommerce.gold_product_funnel;

COUNT(*) 166794

In [0]:
silver_df = spark.table("workspace.ecommerce.silver_events")

In [0]:
# If this is true, you have duplicates
silver_df.count() > silver_df.distinct().count()

True

In [0]:
# Or to find the number of duplicate rows:
total_count = silver_df.count()
distinct_count = silver_df.distinct().count()
print(f"Total rows: {total_count}, Distinct rows: {distinct_count}, Duplicate rows: {total_count - distinct_count}")

Total rows: 42448762, Distinct rows: 42418542, Duplicate rows: 30220


In [0]:
silver_df.display(2)

event_time event_type product_id category_id category_code brand price user_id user_session 2019-10-29T09:17:32.000Z view 1004858 2053013555631882655 electronics.smartphone samsung 131.02 559389453 d71e7146-3d1a-4b96-9d87-fdd314d4694c 2019-10-29T09:17:32.000Z view 1004858 2053013555631882655 electronics.smartphone samsung 131.02 565343162 cfbbc662-af26-4ee7-be22-7a3d507bb2bf 2019-10-29T09:17:33.000Z purchase 5800792 2053013553945772349 electronics.audio.subwoofer null 162.17 536723169 567d676d-5c64-4646-adb2-c8c6ff9fc8fb 2019-10-29T09:17:33.000Z view 1005064 2053013555631882655 electronics.smartphone xiaomi 187.65 513355340 74a71cdb-c262-4f96-8e58-00bfeacf05e3 2019-10-29T09:17:33.000Z view 1003315 2053013555631882655 electronics.smartphone apple 965.17 512786243 3331167a-db7f-4b4a-bc31-30f4c4aa93f3 2019-10-29T09:17:33.000Z view 51800024 2135658542386905834 null tomfarr 121.75 551703117 23ff3e46-7999-4b37-aa3e-8091fc39d1e2 2019-10-29T09:17:33.000Z view 4700478 2053013560899928785 auto.accessories.videoregister sho-me 141.91 512475445 54924b97-2003-46dd-8261-86ef699d9db6 2019-10-29T09:17:33.000Z view 1004249 2053013555631882655 electronics.smartphone apple 725.12 550686150 730e7bc6-3df6-4097-a29f-af3283b3891c 2019-10-29T09:17:33.000Z view 1003747 2053013555631882655 electronics.smartphone sony 282.81 560569926 89ec64f0-f283-4178-8f18-30442a9d128e 2019-10-29T09:17:33.000Z view 1307341 2053013558920217191 computers.notebook asus 617.75 535175444 71c0c0ac-d7e1-4294-a977-1db78caa97b9 2019-10-29T09:17:33.000Z view 1005143 2053013555631882655 electronics.smartphone apple 1543.37 565341518 e345c070-d555-419a-9e5f-a41d2ef79fd5 2019-10-29T09:17:33.000Z view 1005102 2053013555631882655 electronics.smartphone xiaomi 431.92 540806242 d309fe6d-eec6-4f3e-8956-de26f9690d56 2019-10-29T09:17:33.000Z view 26800031 2053013564641248165 null genau 308.61 559474580 437e911f-d4bb-4289-8e55-f009993fd870 2019-10-29T09:17:33.000Z view 4700549 2053013560899928785 auto.accessories.videoregister neoline 143.89 518578763 a2fd7fb9-b49b-4de6-b6a8-debdd0d9763e 2019-10-29T09:17:34.000Z view 7004521 2053013560346280633 kids.carriage alis 102.94 533844288 bce47fc3-8a37-4b25-97e8-0af19118d678 2019-10-29T09:17:34.000Z purchase 4300285 2053013552385491165 null electrolux 107.53 517022373 e004cfc0-7603-4939-b77f-b539216ac4aa 2019-10-29T09:17:34.000Z view 1005121 2053013555631882655 electronics.smartphone apple 1000.8 519265307 7ca20ecd-ff9c-42cb-94be-19ce14eff943 2019-10-29T09:17:34.000Z view 1004767 2053013555631882655 electronics.smartphone samsung 243.22 564915110 42608c70-59ee-48ea-930d-3b9bf5e2e2c2 2019-10-29T09:17:34.000Z view 1500076 2053013552955916539 computers.peripherals.printer samsung 98.58 546205967 6f95e9eb-0c45-4c13-a33b-4c02c5706fe6 2019-10-29T09:17:34.000Z view 35108648 2070005009382114061 apparel.underwear milavitsa 20.49 559744084 d60a297a-8629-484c-b0bf-fb28973df210 2019-10-29T09:17:34.000Z view 1500021 2053013552955916539 computers.peripherals.printer epson 116.55 514343184 4736f372-162b-4b6f-980b-c1449b0b7201 2019-10-29T09:17:34.000Z view 7006284 2053013560346280633 kids.carriage null 72.07 542929356 274039b2-b2f4-448c-878e-f79792c59bee 2019-10-29T09:17:34.000Z view 1004489 2053013555631882655 electronics.smartphone huawei 123.8 535539432 ecea61d7-f5fa-4bc6-8837-d102bc28ec1a 2019-10-29T09:17:34.000Z view 14700716 2053013557133443581 furniture.living_room.cabinet null 159.05 518026348 ed1751b7-df95-40e9-8d88-e82d6bb7ff84 2019-10-29T09:17:34.000Z view 8801100 2053013555573162395 electronics.telephone nokia 94.65 528330570 d0721bca-2613-4035-a170-8ef623550a46 2019-10-29T09:17:34.000Z view 26018454 2053013562611204913 null null 5.22 512531233 72b5ef12-75e4-4df5-8376-63f801a6c1e1 2019-10-29T09:17:34.000Z view 13300108 2053013557166998015 null null 115.81 536830428 fed08046-7036-4ead-9bc9-ded313df6d4c 2019-10-29T09:17:34.000Z view 3600937 2053013563810775923 appliances.kitchen.washer samsung 334.6 516542439 4428df80-aec7-490a-88f9-03fb8d0a177c 2019-10

In [0]:
silver_dedup_df = silver_df.dropDuplicates(["user_session", "event_time", "product_id"])

In [0]:
# Or to find the number of duplicate rows:
total_count = silver_dedup_df.count()
distinct_count = silver_dedup_df.distinct().count()
print(f"Total rows: {total_count}, Distinct rows: {distinct_count}, Duplicate rows: {total_count - distinct_count}")

Total rows: 42412833, Distinct rows: 42412833, Duplicate rows: 0


In [0]:
silver_dedup_df.write.format("delta") \
    .mode("overwrite") \
    .saveAsTable("workspace.ecommerce.silver_events")